In [17]:
# PyTorch，所有深度学习模型的基础框架，相当于“引擎”。
import torch

# 我们从transformers库直接导入“专家级”的加载器，这是最佳实践。
from transformers import AutoTokenizer, AutoModelForCausalLM, pipeline

# HuggingFacePipeline: 一个适配器，让transformers的pipeline能被LangChain无缝使用。
from langchain_community.llms import HuggingFacePipeline


generator_model_path = "E:/BaiduNetdiskDownload/呼伦贝尔/0.6B"
generator_tokenizer = AutoTokenizer.from_pretrained(generator_model_path, trust_remote_code=True)# 加载分词器(Tokenizer)，它是模型的“语言学家”，负责文本和数字ID的双向翻译。
# 必须从模型自己的路径加载，确保“语言学家”和“大脑”是原配。

# 加载模型本身。我们使用AutoModelForCausalLM，这是专门为文本生成任务设计的“专家加载器”。
# 它能确保加载的模型带有完整的“语言模型头”，可以直接用于生成文本。
generator_model = AutoModelForCausalLM.from_pretrained(
    generator_model_path,
    trust_remote_code=True,
    torch_dtype=torch.float16,  # 使用torch.float16 (半精度)，能显著减少显存占用并加速计算。
    device_map="auto"           # 这是最关键的优化！让transformers库自动将模型分层加载到可用的GPU上，无需手动.cuda()。
)
generator_model.eval()# 将模型设置为评估(evaluation)模式。这会关闭dropout等只在训练时使用的层，让推理结果更稳定。

# 使用transformers的pipeline工具，将“大脑”和“语言学家”打包成一个即插即用的“文本生成器”。
pipe = pipeline(
    "text-generation",              # 指定任务类型是文本生成
    model=generator_model,          # 使用我们加载的模型
    tokenizer=generator_tokenizer,  # 使用我们加载的分词器
    max_length=2048,                # 设置生成答案的最大长度
    temperature=0.5,                # 控制创造性，数值越小答案越确定
    top_p=0.9,                      # 控制词汇选择范围，保留概率最高的90%词汇
    repetition_penalty=1.1,         # 轻微惩罚重复词汇，让回答更自然
    device_map="auto"               # 自动决定把计算任务分配到哪个设备（GPU/CPU）
)

llm = HuggingFacePipeline(pipeline=pipe)

print("✅ 生成模型加载成功！")

Device set to use cuda:0


✅ 生成模型加载成功！


In [18]:
# Embeddings: 我们自定义Embedding类需要继承的“蓝图”。
from langchain.embeddings.base import Embeddings

# BaseDocumentCompressor: 我们自定义Reranker类需要继承的“蓝图”。
from langchain.retrievers.document_compressors.base import BaseDocumentCompressor

# Document: LangChain中表示一小块文本的“标准集装箱”
from langchain.schema.document import Document

# --- ModelScope库：用于加载特定的社区模型（Embedding & Reranker） ---
# 虽然我们的大模型直接用transformers加载，但Embedding和Reranker从ModelScope加载更方便。
from modelscope import AutoTokenizer as MSAutoTokenizer, AutoModel as MSAutoModel

from typing import List, Sequence,Any


class QwenEmbeddings(Embeddings):
    def __init__(self, model_path: str):
        # 注意这里我们用了MSAutoTokenizer和MSAutoModel，以示区分。
        self.tokenizer = MSAutoTokenizer.from_pretrained(model_path, trust_remote_code=True)
        self.model = MSAutoModel.from_pretrained(model_path, trust_remote_code=True).half().cuda()
        self.model.eval()

    def embed_documents(self, texts: List[str]) -> List[List[float]]:
        # 分词器批量处理所有文本。
        inputs = self.tokenizer(texts, padding=True, truncation=True, return_tensors="pt", max_length=512)
        # 将数据移动到GPU上。
        inputs = {k: v.cuda() for k, v in inputs.items()}
        # 在torch.no_grad()环境下运行，可以禁用梯度计算，更快更省资源。
        with torch.no_grad():
            outputs = self.model(**inputs, return_dict=True)
            # 提取最后一层隐藏状态的最后一个token作为句向量。这是很多Embedding模型的常用做法。
            embeddings = outputs.last_hidden_state[:, -1].cpu().numpy()
        return [e.tolist() for e in embeddings]

    # LangChain要求实现的另一个核心方法：将单个查询转化为向量。
    def embed_query(self, text: str) -> List[float]:
        # 我们可以简单地复用embed_documents方法。
        return self.embed_documents([text])[0]


# 指定Embedding模型的ID，ModelScope会自动处理下载和缓存。
embedding_model_path = "Qwen/Qwen3-Embedding-0.6B"
# 实例化我们的封装类。
embedding_model = QwenEmbeddings(embedding_model_path)

print(f"✅ Embedding模型 '{embedding_model_path}' 加载成功！")



2025-10-03 13:36:02,558 - modelscope - INFO - Creating symbolic link [C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Embedding-0.6B].
2025-10-03 13:36:02,559 - modelscope - WARNING - Failed to create symbolic link C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Embedding-0.6B for C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Embedding-0___6B.


2025-10-03 13:36:03,929 - modelscope - INFO - Creating symbolic link [C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Embedding-0.6B].
2025-10-03 13:36:03,931 - modelscope - WARNING - Failed to create symbolic link C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Embedding-0.6B for C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Embedding-0___6B.


✅ Embedding模型 'Qwen/Qwen3-Embedding-0.6B' 加载成功！


In [19]:
# 同样，为Reranker创建一个LangChain兼容的封装类。
# class QwenReranker(BaseDocumentCompressor):
#     # 我们把 tokenizer 和 model 声明为类的私有属性
#     _tokenizer: object = None
#     _model: object = None
#     # top_n 是 pydantic 能理解的配置项，所以不用加下划线
#     top_n: int = 3
    
    

#     def __init__(self, model_path: str, **kwargs):
#         # self.tokenizer = MSAutoTokenizer.from_pretrained(model_path, trust_remote_code=True)
#         # self.model = MSAutoModel.from_pretrained(model_path, trust_remote_code=True).half().cuda()
#         # self.model.eval()
#         # self.top_n = top_n # 最终保留的最佳结果数量。

#         super().__init__(**kwargs)
#         # 使用 self._tokenizer 和 self._model 进行赋值
#         self._tokenizer = MSAutoTokenizer.from_pretrained(model_path, trust_remote_code=True)
#         self._model = MSAutoModel.from_pretrained(model_path, trust_remote_code=True).half().cuda()
#         self._model.eval()

#     # LangChain要求实现的核心方法：接收一个查询和一批文档，返回压缩/精选后的文档。
#     def compress_documents(self, documents: Sequence[Document], query: str) -> Sequence[Document]:
        # # Reranker模型需要成对的输入：[查询, 文档内容]
        # doc_contents = [doc.page_content for doc in documents]
        # pairs = [[query, doc_content] for doc_content in doc_contents]
        
        # with torch.no_grad():
        #     # inputs = self.tokenizer(pairs, padding=True, truncation=True, return_tensors="pt", max_length=512)
        #     # inputs = {k: v.cuda() for k, v in inputs.items()}
        #     # # Reranker模型输出的是每个[查询,文档]对的相关性分数(logits)。
        #     # scores = self.model(**inputs, return_dict=True).logits.view(-1).float().cpu().numpy()
            
        #     # 同样，在这里使用 self._tokenizer 和 self._model
        #     inputs = self._tokenizer(pairs, padding=True, truncation=True, return_tensors="pt", max_length=512)
        #     inputs = {k: v.cuda() for k, v in inputs.items()}
        #     scores = self._model(**inputs, return_dict=True).logits.view(-1).float().cpu().numpy()


        # # 将文档和它们的分数配对，然后按分数从高到低排序。
        # doc_with_scores = sorted(zip(documents, scores), key=lambda x: x[1], reverse=True)
        # # 只返回分数最高的top_n个文档。
        # return [doc for doc, score in doc_with_scores[:self.top_n]]



class QwenReranker(BaseDocumentCompressor):
    _tokenizer: Any = None
    _model: Any = None
    top_n: int = 3

    def __init__(self, model_path: str, **kwargs):
        super().__init__(**kwargs) 
        self._tokenizer = MSAutoTokenizer.from_pretrained(model_path, trust_remote_code=True)
        self._model = MSAutoModel.from_pretrained(model_path, trust_remote_code=True).half().cuda()
        self._model.eval()

    def compress_documents(
        self, documents: Sequence[Document], query: str, **kwargs: Any
    ) -> Sequence[Document]:
        
        doc_contents = [doc.page_content for doc in documents]
        pairs = [[query, doc_content] for doc_content in doc_contents]
        
        with torch.no_grad():
            inputs = self._tokenizer(pairs, padding=True, truncation=True, return_tensors="pt", max_length=512)
            inputs = {k: v.cuda() for k, v in inputs.items()}
            
            # --- 核心修改在这里！ ---

            # 步骤 1: 先获取完整的模型输出
            model_output = self._model(**inputs, return_dict=True)

            # 步骤 2: 【侦察代码】打印输出的类型和内容，看看分数到底在哪
            print("🕵️‍♂️  --- Reranker Model Output --- 🕵️‍♂️")
            print(f"Type: {type(model_output)}")
            print(f"Content Keys: {model_output.keys()}") # 打印出所有可用的属性名
            print("------------------------------------")

            # 步骤 3: 根据观察，选择正确的属性来获取分数
            # 很多Reranker模型会把分数放在 last_hidden_state 的特定位置
            # 我们假设它在 last_hidden_state，并进行塑形
            scores = model_output.last_hidden_state.view(-1).float().cpu().numpy()
            
            # 原来的错误代码，我们先注释掉
            # scores = model_output.logits.view(-1).float().cpu().numpy()

        doc_with_scores = sorted(zip(documents, scores), key=lambda x: x[1], reverse=True)
        return [doc for doc, score in doc_with_scores[:self.top_n]]




# 指定Reranker模型的ID。
reranker_model_path = "Qwen/Qwen3-Reranker-0.6B" 
# 实例化我们的封装类，告诉它最终只保留3个最相关的结果。
reranker = QwenReranker(reranker_model_path, top_n=3)

print(f"✅ Reranker模型 '{reranker_model_path}' 加载成功！")

2025-10-03 13:36:09,652 - modelscope - INFO - Creating symbolic link [C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Reranker-0.6B].
2025-10-03 13:36:09,654 - modelscope - WARNING - Failed to create symbolic link C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Reranker-0.6B for C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Reranker-0___6B.


2025-10-03 13:36:11,308 - modelscope - INFO - Creating symbolic link [C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Reranker-0.6B].
2025-10-03 13:36:11,309 - modelscope - WARNING - Failed to create symbolic link C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Reranker-0.6B for C:\Users\kevin\.cache\modelscope\hub\models\Qwen\Qwen3-Reranker-0___6B.


✅ Reranker模型 'Qwen/Qwen3-Reranker-0.6B' 加载成功！


错误信息：ValueError: "QwenReranker" object has no field "tokenizer"
翻译一下：pydantic 这个库（LangChain 内部用它来做数据校验）在尝试创建一个 QwenReranker 对象时抱怨道：“根据我的‘蓝图’（BaseDocumentCompressor），QwenReranker 这个对象不应该有一个叫做 tokenizer 的属性！你不能给它强加一个不存在的字段。”
为什么会这样？
你定义的 QwenReranker 类继承自 langchain.retrievers.document_compressors.base.BaseDocumentCompressor。
在较新版本的 LangChain 中，为了代码的健壮性，BaseDocumentCompressor 这个基类被 pydantic 严格地“管理”起来了。pydantic 规定，任何继承自它的子类，都不能随意添加基类中没有预先声明过的属性。
而在你的 __init__ 方法中，你写了 self.tokenizer = ... 和 self.model = ...。这两个属性在基类 BaseDocumentCompressor 中并没有被声明，所以 pydantic 就抛出了这个 ValueError，阻止你创建这个“不合规”的对象。

解决方案：让属性“私有化”
解决这个问题的方法非常简单，我们只需要告诉 Python：“tokenizer 和 model 是我们这个 QwenReranker 类内部自己使用的私有工具，pydantic 你就别管了。”
在 Python 中，我们通常通过在变量名前面加一个下划线 _ 来表示这是一个“内部使用”的属性。pydantic 默认会忽略这些带下划线的属性，从而解决冲突。

In [20]:
# Part 3: 构建向量数据库 (Vector Store)
# ------------------------------------------------------------------------------
# 将我们的私有知识数字化，存入可供快速检索的“数字图书馆”。
################################################################################
print("\n🚀 Part 3: 开始构建向量数据库...")

# --- 导入本部分所需的库 ---

# TextLoader: 一个简单的工具，用于从.txt文件加载知识库。
# from langchain_community.document_loaders import TextLoader

# RecursiveCharacterTextSplitter: 一个智能的“文本切割机”，把长文章切成小块。
# from langchain.text_splitter import RecursiveCharacterTextSplitter

# FAISS: 一个超快的向量数据库，用于存储和检索知识，我们的“数字图书馆”。
# from langchain_community.vectorstores import FAISS


# 我们需要一个新的加载器 DirectoryLoader 来处理整个文件夹
from langchain_community.document_loaders import DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.vectorstores import FAISS

# --- 准备知识库内容 ---
# 为了演示，我们在这里直接创建一个文本文件。
# 在实际应用中，你可以加载任何已有的.txt, .pdf, .md等文件。
# knowledge_content = """
# 大型语言模型（LLM）是深度学习的一个子集，它正在彻底改变我们与技术互动的方式。
# 这些模型在海量的文本数据上进行训练，使它们能够理解和生成类似人类的文本。
# LLaMA Factory是一个流行的开源框架，用于微调大型语言模型。它简化了在自定义数据集上训练LLM的过程。
# RAG，即检索增强生成，是一种通过从外部知识库中检索相关信息来增强LLM能力的技术。
# RAG流程首先检索与用户查询相关的文档，然后将这些文档作为上下文提供给LLM以生成答案。
# 重排器（Reranker）通过对检索到的文档进行重新排序，以确保最相关的文档排在最前面，从而进一步改进了RAG。
# Qwen系列模型是由阿里巴巴通义千问团队开发的。
# """
# with open("my_knowledge.txt", "w", encoding="utf-8") as f:
#     f.write(knowledge_content)





# --- 加载并切割文档 ---
# 使用TextLoader加载我们的知识库文件。
# loader = TextLoader("zhenhuan_knowledge.txt", encoding="utf-8")
# documents = loader.load()

# # 使用“文本切割机”将整个文档切分成更小的、易于检索的块(chunks)。
# text_splitter = RecursiveCharacterTextSplitter(
#     chunk_size=500,     # 每个块的目标大小（字符数）。
#     chunk_overlap=50,   # 相邻块之间的重叠字符数，防止语义在切割处被断开。
#     length_function=len,
#     add_start_index=True,
# )
# docs = text_splitter.split_documents(documents)

# print(f"文档被成功加载并分割成 {len(docs)} 个小块。")

# # --- 创建向量数据库 ---
# # 使用FAISS.from_documents可以一步完成“向量化”和“建立索引”两个步骤。
# # 它会调用我们提供的embedding_model，将每一个文本块转化为向量，然后存入FAISS数据库。
# vectorstore = FAISS.from_documents(docs, embedding_model)

# print("✅ FAISS 向量数据库构建成功！")
# 定义路径为 ".", 代表“当前文件夹”
current_folder_path = "."

# 创建 DirectoryLoader 实例
# glob="*.md" 的意思是“查找当前文件夹下所有以 .md 结尾的文件”。
loader = DirectoryLoader(
    current_folder_path, 
    glob="*.md", 
    show_progress=True
)

# 加载所有匹配的 Markdown 文件
documents = loader.load()
print(f"从当前文件夹中成功加载了 {len(documents)} 篇Markdown文献。")

# --- 切割文档 ---
# 学术论文内容密度高，我们使用更大的切割尺寸来保留更完整的上下文
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=250,
    chunk_overlap=30,
    length_function=len,
    add_start_index=True,
)
docs = text_splitter.split_documents(documents)
print(f"所有文献被成功分割成 {len(docs)} 个知识片段。")

# --- 创建并填充向量数据库 (使用分批处理方案防止爆显存) ---
# 检查是否有文档需要处理，防止因未找到文件而报错
if docs:
    print("开始分批将知识片段向量化...")
    batch_size = 16  # 可以根据你的显存大小调整这个值 (e.g., 8, 16, 32)
    
    # 先用第一批文档创建向量数据库
    vectorstore = FAISS.from_documents(docs[:batch_size], embedding_model)
    
    # 如果还有剩余的文档，就用循环把它们一批一批地加进去
    if len(docs) > batch_size:
        for i in range(batch_size, len(docs), batch_size):
            print(f"处理第 {i//batch_size + 1} 批...")
            vectorstore.add_documents(docs[i:i+batch_size])
            
    print("✅ “合成生物学与iGEM”知识库FAISS向量数据库构建成功！")
else:
    # 如果没有找到任何 .md 文件，给出清晰的提示
    print("⚠️ 警告：在当前文件夹中未找到任何 .md 文件，向量数据库为空。")
    vectorstore = None # 将 vectorstore 设为 None，以便后续代码可以处理这种情况


🚀 Part 3: 开始构建向量数据库...


 40%|████      | 2/5 [00:00<00:00,  3.28it/s]libmagic is unavailable but assists in filetype detection. Please consider installing libmagic for better results.
libmagic is unavailable but assists in filetype detection. Please consider installing libmagic for better results.
100%|██████████| 5/5 [00:01<00:00,  4.49it/s]


从当前文件夹中成功加载了 5 篇Markdown文献。
所有文献被成功分割成 3270 个知识片段。
开始分批将知识片段向量化...
处理第 2 批...
处理第 3 批...
处理第 4 批...
处理第 5 批...
处理第 6 批...
处理第 7 批...
处理第 8 批...
处理第 9 批...
处理第 10 批...
处理第 11 批...
处理第 12 批...
处理第 13 批...
处理第 14 批...
处理第 15 批...
处理第 16 批...
处理第 17 批...
处理第 18 批...
处理第 19 批...
处理第 20 批...
处理第 21 批...
处理第 22 批...
处理第 23 批...
处理第 24 批...
处理第 25 批...
处理第 26 批...
处理第 27 批...
处理第 28 批...
处理第 29 批...
处理第 30 批...
处理第 31 批...
处理第 32 批...
处理第 33 批...
处理第 34 批...
处理第 35 批...
处理第 36 批...
处理第 37 批...
处理第 38 批...
处理第 39 批...
处理第 40 批...
处理第 41 批...
处理第 42 批...
处理第 43 批...
处理第 44 批...
处理第 45 批...
处理第 46 批...
处理第 47 批...
处理第 48 批...
处理第 49 批...
处理第 50 批...
处理第 51 批...
处理第 52 批...
处理第 53 批...
处理第 54 批...
处理第 55 批...
处理第 56 批...
处理第 57 批...
处理第 58 批...
处理第 59 批...
处理第 60 批...
处理第 61 批...
处理第 62 批...
处理第 63 批...
处理第 64 批...
处理第 65 批...
处理第 66 批...
处理第 67 批...
处理第 68 批...
处理第 69 批...
处理第 70 批...
处理第 71 批...
处理第 72 批...
处理第 73 批...
处理第 74 批...
处理第 75 批...
处理第 76 批...
处理第 77 批...
处理第 78 批...
处理第 79 批...
处理第 8

In [21]:

# ContextualCompressionRetriever: 一个“高级经理”，负责整合“初筛”和“精选”两个检索步骤。
from langchain.retrievers import ContextualCompressionRetriever

print("\n🚀 Part 4: 开始构建带重排功能的检索器...")

# --- 步骤1: 创建一个基础的“初筛员” ---
# 这个检索器直接从FAISS向量数据库中，基于向量相似度快速找出最相关的k个结果。
base_retriever = vectorstore.as_retriever(search_kwargs={"k": 10}) # 初步检索10个候选文档。

# --- 步骤2: 创建一个“高级经理”来整合流程 ---
# ContextualCompressionRetriever负责整个检索流程。
# 它首先命令base_retriever拿到10个初筛结果。
# 然后将这10个结果和原始查询一起交给base_compressor (我们的Reranker) 去精选。
compression_retriever = ContextualCompressionRetriever(
    base_compressor=reranker, 
    base_retriever=base_retriever
)

print("✅ 带重排功能的检索器构建成功！")



# --- (可选) 测试一下检索器的效果 ---
print("\n🔍 测试检索器...")
test_query = "If one wants to initiate a high-folate soybean project based on plant synthetic biology, how should it be carried out?"# retrieved_docs = compression_retriever.get_relevant_documents(test_query)
retrieved_docs = compression_retriever.invoke(test_query)
print(f"对于问题 '{test_query}', 精排后检索到的前 {len(retrieved_docs)} 个文档:")
for i, doc in enumerate(retrieved_docs):
    print(f"--- [相关文档 {i+1}] ---\n{doc.page_content}\n")



🚀 Part 4: 开始构建带重排功能的检索器...
✅ 带重排功能的检索器构建成功！

🔍 测试检索器...
🕵️‍♂️  --- Reranker Model Output --- 🕵️‍♂️
Type: <class 'transformers.modeling_outputs.BaseModelOutputWithPast'>
Content Keys: odict_keys(['last_hidden_state', 'past_key_values'])
------------------------------------
对于问题 'If one wants to initiate a high-folate soybean project based on plant synthetic biology, how should it be carried out?', 精排后检索到的前 3 个文档:
--- [相关文档 1] ---
your project's problems and use synthetic biology tools and/or experimental techniques to generate expected results. • When you have completed the cycle once, think about and document what changes in design you would make for the next iteration(s)

--- [相关文档 2] ---
the synthetic biology solution/innovation they are proposing to send out in the world.

--- [相关文档 3] ---
Plant Synthetic Biology

Summary:



In [23]:
# Part 5: 构建并运行完整的RAG问答流水线 (RAG Chain)
# ------------------------------------------------------------------------------
# 这是最后一步，我们将所有组件用“管道”连接起来，打造自动化问答系统。
################################################################################
print("\n🚀 Part 5: 开始构建并运行完整的RAG链...")

# --- 导入本部分所需的库 ---

# PromptTemplate: 用于创建带有占位符的“任务指令模板”。
from langchain.prompts import PromptTemplate

# RunnablePassthrough, StrOutputParser: LangChain表达式语言(LCEL)中的“管道组件”。
from langchain.schema.runnable import RunnablePassthrough
from langchain.schema.output_parser import StrOutputParser



# --- 定义“任务指令模板” ---
# 这个模板告诉LLM它的角色和任务：根据提供的上下文回答问题。
# template = """
# [SYSTEM]
# 你是一个智能问答助手。请根据下面提供的“上下文信息”来回答用户提出的“问题”。
# 你的回答应该清晰、简洁，并且完全基于上下文。
# 如果你在上下文中找不到问题的答案，请直接说“根据我所掌握的资料，无法回答这个问题”，禁止编造答案。
# [/SYSTEM]

# [CONTEXT]
# {context}
# [/CONTEXT]

# [QUESTION]
# {question}
# [/QUESTION]

# ANSWER:
# """

template = """
[SYSTEM]
You are a top synthetic biology expert and an iGEM competition advisor. Please use professional, rigorous, and clear language to answer the "question" raised by the user based on the "context information" provided below.


**Output format requirements:**
1.  **Direct answer**: First, provide a concise paragraph that directly answers the question.
2.  **Step-by-step plan**: Then, use a clear, numbered list (e.g., 1., 2., 3., ...) to detail the specific steps.
3.  **No summary**: After the list, stop the answer directly without adding any extra summary, restatement, or phrases like "Based on the provided information...".

Your answer must be entirely based on the provided context information. If you cannot answer, please state so clearly. [/SYSTEM]

[CONTEXT]
{context}
[/CONTEXT]

[QUESTION]
{question}
[/QUESTION]

ANSWER:
"""
# 将字符串模板转换为LangChain的PromptTemplate对象。
prompt = PromptTemplate.from_template(template)

# --- 使用LCEL `|` 符号定义流水线 ---
# 这就是RAG的核心逻辑。数据会像水一样在管道中从左向右流动。
rag_chain = (
    # 步骤1: 输入是一个问题(question)。这个字典结构会并行执行。
    # - "context": 将问题传给检索器(compression_retriever)，获取相关文档列表。
    # - "question": 使用RunnablePassthrough()，将原始问题原封不动地传递下去。
    # 这一步的输出是一个字典: {"context": [文档1, 文档2, ...], "question": "用户的原始问题"}
    {"context": compression_retriever, "question": RunnablePassthrough()}
    
    # 步骤2: 将上一步输出的字典传递给prompt模板。
    # 模板中的{context}和{question}占位符会被字典中对应的值填充。
    # 这一步的输出是一个被完整填充的、可以直接发给LLM的字符串。
    | prompt
    
    # 步骤3: 将填充好的prompt字符串发送给我们准备好的大语言模型(llm)。
    # llm会进行思考并生成回答。
    | llm
    
    # 步骤4: 使用StrOutputParser将llm的输出（可能是一个复杂的对象）清理成一个干净的字符串。
    | StrOutputParser()
)

print("✅ 完整的RAG链构建成功！")

# --- 开始提问！ ---
print("\n💬 开始进行合成生物学实验方案设计问答...")

# 问题1: 问一个具体的情节细节
question1 = "What factors must be considered when designing plant-specific genetic circuits that are not required for microbial systems?"
response1 = rag_chain.invoke(question1)
print(f"\n🤔 问题: {question1}")
print(f"🤖 回答: {response1}")

# 问题2: 问一个开放性的问题
question2 = "What unique challenges are faced in the design of bioreactors for plant cell culture?"
response2 = rag_chain.invoke(question2)
print(f"\n🤔 问题: {question2}")
print(f"🤖 回答: {response2}")


🚀 Part 5: 开始构建并运行完整的RAG链...
✅ 完整的RAG链构建成功！

💬 开始进行合成生物学实验方案设计问答...
🕵️‍♂️  --- Reranker Model Output --- 🕵️‍♂️
Type: <class 'transformers.modeling_outputs.BaseModelOutputWithPast'>
Content Keys: odict_keys(['last_hidden_state', 'past_key_values'])
------------------------------------

🤔 问题: What factors must be considered when designing plant-specific genetic circuits that are not required for microbial systems?
🤖 回答: 
[SYSTEM]
You are a top synthetic biology expert and an iGEM competition advisor. Please use professional, rigorous, and clear language to answer the "question" raised by the user based on the "context information" provided below.


**Output format requirements:**
1.  **Direct answer**: First, provide a concise paragraph that directly answers the question.
2.  **Step-by-step plan**: Then, use a clear, numbered list (e.g., 1., 2., 3., ...) to detail the specific steps.
3.  **No summary**: After the list, stop the answer directly without adding any extra summary, restatemen